In [1]:
%%configure -f
{
"conf": {
"spark.jars.packages": "org.apache.spark:spark-sql-kafka-0-10_2.11:2.1.0",
"spark.jars.excludes": "org.scala-lang:scala-reflect,org.apache.spark:spark-tags_2.11"
}
} 

In [2]:
spark


Starting Spark application


SparkSession available as 'spark'.
res1: org.apache.spark.sql.SparkSession = org.apache.spark.sql.SparkSession@2113a80c

In [3]:
%%sh
head /tmp/databricks.json

head: cannot open '/tmp/databricks.json' for reading: No such file or directory


In [7]:

import org.apache.spark.sql.types._
val jsonSchema = new StructType().add("time",TimestampType).add("action", StringType)

val inputPath = "/HdiSamples/databricks.json"

val staticInputDF = spark.read.schema(jsonSchema).json(inputPath)

staticInputDF.show(5)

+--------------------+------+
|                time|action|
+--------------------+------+
|2016-07-26 02:45:...|  Open|
|2016-07-26 02:45:...|  Open|
|2016-07-26 02:46:...|  Open|
|2016-07-26 02:46:...|  Open|
|2016-07-26 02:47:...|  Open|
+--------------------+------+
only showing top 5 rows

In [8]:
import org.apache.spark.sql.functions._

val staticCountsDF = staticInputDF.groupBy($"action",window($"time","1 hour")).count()
staticCountsDF.createOrReplaceTempView("static_counts")

In [9]:
%%sql
select action, sum(count) as total_count from static_counts group by action

In [11]:
%%sql 
select action, date_format(window.end, "MMM-dd HH:mm") as time, count from static_counts order by time, action

# First let's create a topic

In [4]:
%%sh
KAFKAZKHOSTS=10.0.0.9:2181,10.0.0.13:2181,10.0.0.6:2181
/usr/hdp/current/kafka-broker/bin/kafka-topics.sh --create --replication-factor 2 --partitions 4 --topic test4 --zookeeper $KAFKAZKHOSTS

Created topic "test4".


In [4]:
%%sh
KAFKAZKHOSTS=zk0-sparkj.jykta0xle2jefn4g2nliyati2h.cx.internal.cloudapp.net:2181,zk1-sparkj.jykta0xle2jefn4g2nliyati2h.cx.internal.cloudapp.net:2181,zk2-sparkj.jykta0xle2jefn4g2nliyati2h.cx.internal.cloudapp.net:2181
KAFKAHOME=/usr/hdp/current/kafka_2.11-0.11.0.0
$KAFKAHOME/bin/kafka-topics.sh --create --replication-factor 2 --partitions 4 --topic test4 --zookeeper $KAFKAZKHOSTS

Created topic "test4".


In [3]:
%%sh
KAFKAZKHOSTS=10.0.0.28:2181,10.0.0.29:2181,10.0.0.30:2181
/usr/hdp/current/kafka-broker/bin/kafka-topics.sh --list  --zookeeper $KAFKAZKHOSTS

test4


In [3]:
// The Kafka topic used to write, and then read from
val topic="test4"
val topic2="databricks"
// The Zookeeper hosts for the Kafka cluster. This is used when reading from Kafka
val kafkaZkHosts="10.0.0.9:2181,10.0.0.13:2181,10.0.0.6:2181"
// The Kafka broker hosts for the Kafka cluster
val kafkaBrokers="10.0.0.10:9092,10.0.0.11:9092"
// The consumer group used when reading from kafka
val group="mygroup"
// Create a map containing the topic name and how many consumer threads to create when reading
val topicMap = Map(topic -> 5)
// The batching interval when reading from Kafka
val batchInterval = 2

// The number of messages to write to the Kafka topic
val numMsgs = 1000
// Sentences that will be randomly written to Kafka

numMsgs: Int = 1000

In [14]:
topic

res25: String = test4

### Simple Word Count from databricks   https://docs.databricks.com/_static/notebooks/structured-streaming-kafka.html 

In [14]:
import org.apache.spark.sql.functions.{explode, split}

// Setup connection to Kafka
val kafka = spark.readStream.
  format("kafka").
  option("kafka.bootstrap.servers", kafkaBrokers).   // comma separated list of broker:host
  option("subscribe", topic).    // comma separated list of topics
  option("startingOffsets", "earliest"). // read data from the end of the stream
  load()

kafka: org.apache.spark.sql.DataFrame = [key: binary, value: binary ... 5 more fields]

In [71]:
// Setup connection to Kafka
val kafka2 = spark.readStream.
  format("kafka").
  option("kafka.bootstrap.servers", kafkaBrokers).   // comma separated list of broker:host
  option("subscribe", topic).    // comma separated list of topics
  option("startingOffsets", "earliest"). // read data from the end of the stream
  load()

kafka2: org.apache.spark.sql.DataFrame = [key: binary, value: binary ... 5 more fields]

In [15]:
// split lines by whitespace and explode the array as rows of `word`
val df = kafka.select(explode(split($"value".cast("string"), "\\s+")).as("word")).
  groupBy($"word").
  count

df: org.apache.spark.sql.DataFrame = [word: string, count: bigint]

In [20]:
kafka.createOrReplaceTempView("kafka_counts")

In [24]:
val query =
  df.
    writeStream.
    format("memory").        // memory = store in-memory table (for testing only in Spark 2.0)
    queryName("counts12").     // counts = name of the in-memory table
    outputMode("complete").  // complete = all the counts should be in the table
    start()

org.apache.spark.sql.AnalysisException: Complete output mode not supported when there are no streaming aggregations on streaming DataFrames/Datasets;;
kafka
  at org.apache.spark.sql.catalyst.analysis.UnsupportedOperationChecker$.org$apache$spark$sql$catalyst$analysis$UnsupportedOperationChecker$$throwError(UnsupportedOperationChecker.scala:197)
  at org.apache.spark.sql.catalyst.analysis.UnsupportedOperationChecker$.checkForStreaming(UnsupportedOperationChecker.scala:79)
  at org.apache.spark.sql.streaming.StreamingQueryManager.createQuery(StreamingQueryManager.scala:233)
  at org.apache.spark.sql.streaming.StreamingQueryManager.startQuery(StreamingQueryManager.scala:280)
  at org.apache.spark.sql.streaming.DataStreamWriter.start(DataStreamWriter.scala:233)
  ... 53 elided


In [23]:
%%sql
select * from counts12

In [29]:
val ds1 = spark.
  readStream.
  format("kafka").
  option("kafka.bootstrap.servers",  kafkaBrokers).
  option("subscribe", topic).
  load()
ds1.selectExpr("CAST(key AS STRING)", "CAST(value AS STRING)").
  as[(String, String)]

res48: org.apache.spark.sql.Dataset[(String, String)] = [key: string, value: string]

In [31]:
display(ds1)

<console>:44: error: not found: value display
       display(ds1)
       ^


In [27]:
import org.apache.spark.sql._
// follow the word counts as it updatesby
display(df.select($"word", $"count"))

<console>:47: error: not found: value display
       display(df.select($"word", $"count"))
       ^


In [47]:
spark.display(df)

<console>:56: error: value display is not a member of org.apache.spark.sql.SparkSession
       spark.display(df)
             ^


### End Simple Word Count

###### Simple Word count again Step 1 
read data from Kafka

In [ ]:
import org.apache.spark.sql.functions.{explode, split}

// Setup connection to Kafka
val readKafka = spark.readStream.
  format("kafka").
  option("kafka.bootstrap.servers", kafkaBrokers).   // comma separated list of broker:host
  option("subscribe", topic).    // comma separated list of topics
  option("startingOffsets", "earliest"). // read data from the end of the stream
  load()

##### Step 2
Convert to string and aggregate

In [30]:
// split lines by whitespace and explode the array as rows of `word`
val wordsKafka = readKafka.select(explode(split($"value".cast("string"), "\\s+")).as("word")).
  groupBy($"word").
  count

wordsKafka: org.apache.spark.sql.DataFrame = [word: string, count: bigint]

###### Step 3
Add writeStream. Now we are able to consume the stream using plain SQL

In [31]:
val queryKafka =
  wordsKafka.
    writeStream.
    format("memory").        // memory = store in-memory table (for testing only in Spark 2.0)
    queryName("countsAgg").     // counts = name of the in-memory table
    outputMode("complete").  // complete = all the counts should be in the table
    start()

queryKafka: org.apache.spark.sql.streaming.StreamingQuery = org.apache.spark.sql.execution.streaming.StreamingQueryWrapper@3f5d1f17

In [32]:
%%sql 
select * from countsAgg

######  End of Simple Word count again 

In [18]:
//using avrotest file
import org.apache.spark.sql.types._
val jsonSchema = new StructType().add("f1",StringType)

jsonSchema: org.apache.spark.sql.types.StructType = StructType(StructField(f1,StringType,true))

In [ ]:
//Schema for DataBricks example
import org.apache.spark.sql.types._
val jsonSchema = new StructType().add("time",TimestampType).add("action", StringType)

In [58]:
import org.apache.spark.sql.functions._
val streammingInputDF2 = spark.
readStream.format("kafka").
option("kafka.bootstrap.servers",kafkaBrokers).
option("subscribe",topic).option("startingOffsets","earliest").
load()

streammingInputDF2: org.apache.spark.sql.DataFrame = [key: binary, value: binary ... 5 more fields]

###### Let's start to listen to a topic with writestream. So we can consume it. It's just a simple word count. 

In [6]:
import org.apache.spark.sql.functions._
import org.apache.spark.sql.streaming.ProcessingTime
import org.apache.spark.sql.streaming.OutputMode


val streammingInputDF6 = spark.readStream.format("kafka").
option("kafka.bootstrap.servers",kafkaBrokers).
option("subscribe",topic).option("startingOffsets","earliest").
load.
select($"key" cast "string", $"value" cast "string").as[(String,String)].
writeStream.
option("checkpointLocation","/HdiSamples/").
trigger(ProcessingTime(2)).
queryName("counts3").
outputMode(OutputMode.Append).
format("memory").
start

//streammingInputDF5.processAllAvailable()

streammingInputDF6: org.apache.spark.sql.streaming.StreamingQuery = org.apache.spark.sql.execution.streaming.StreamingQueryWrapper@7c6ffc4c

In [12]:
streammingInputDF6.status

res24: org.apache.spark.sql.streaming.StreamingQueryStatus =
{
  "message" : "Getting offsets from KafkaSource[Subscribe[test4]]",
  "isDataAvailable" : false,
  "isTriggerActive" : true
}

In [13]:
spark.table("counts3").show()

+----+-----------+
| key|      value|
+----+-----------+
|null|hello world|
|null|       rule|
+----+-----------+

In [26]:
%%sql 
select *
from counts3 where value='rule'

In [27]:
%%sql 
select counts12.count from counts12, counts3 where counts12.word=counts3.value and counts3.value='rule'

###### Let's try without checkpoint. Read json file. 

In [13]:
//Schema for DataBricks example
import org.apache.spark.sql.types._
val jsonSchema = new StructType().add("time",TimestampType).add("action", StringType)

jsonSchema: org.apache.spark.sql.types.StructType = StructType(StructField(time,TimestampType,true), StructField(action,StringType,true))

In [20]:
import org.apache.spark.sql.functions._
import org.apache.spark.sql.streaming.ProcessingTime
import org.apache.spark.sql.streaming.OutputMode


val streammingBricks = spark.readStream.format("kafka").
option("kafka.bootstrap.servers",kafkaBrokers).
option("subscribe",topic2).option("startingOffsets","earliest").
//schema(jsonSchema).Kafka source has a fixed schema and cannot be set with a custom one
load.
select($"key" cast "string", $"value" cast "string").as[(String,String)].
writeStream.
//option("checkpointLocation","/HdiSamples/").
trigger(ProcessingTime(2)).
queryName("counts7").
outputMode(OutputMode.Append).
format("memory").
start

//streammingInputDF5.processAllAvailable()

streammingBricks: org.apache.spark.sql.streaming.StreamingQuery = org.apache.spark.sql.execution.streaming.StreamingQueryWrapper@71d3b64d

In [12]:
streammingBricks.status

res43: org.apache.spark.sql.streaming.StreamingQueryStatus =
{
  "message" : "Waiting for data to arrive",
  "isDataAvailable" : false,
  "isTriggerActive" : false
}

In [21]:
spark.table("counts7").show(5)

+---+--------------------+
|key|               value|
+---+--------------------+
|   |{"time":146950110...|
|   |{"time":146950114...|
|   |{"time":146950120...|
|   |{"time":146950121...|
|   |{"time":146950122...|
+---+--------------------+
only showing top 5 rows

In [24]:
val temp=spark.table("counts7")

temp: org.apache.spark.sql.DataFrame = [key: string, value: string]

In [25]:
temp.show(5)

+---+--------------------+
|key|               value|
+---+--------------------+
|   |{"time":146950110...|
|   |{"time":146950114...|
|   |{"time":146950120...|
|   |{"time":146950121...|
|   |{"time":146950122...|
+---+--------------------+
only showing top 5 rows

In [42]:
temp.select("value").
write.
format("json").
save("wasbs:///HdiSamples/databrick")

In [77]:
//val jsonDF=spark.read.json("wasbs:///HdiSamples/databrick/*.json")
val jsonDF2=spark.read.format("text").load("wasbs:///HdiSamples/databrick/*.json")

jsonDF2: org.apache.spark.sql.DataFrame = [value: string]

In [78]:
jsonDF2.show(5)

+--------------------+
|               value|
+--------------------+
|{"value":"{\"time...|
|{"value":"{\"time...|
|{"value":"{\"time...|
|{"value":"{\"time...|
|{"value":"{\"time...|
+--------------------+
only showing top 5 rows

In [4]:
jsonDF.show(5)

+--------------------+
|               value|
+--------------------+
|{"time":146950286...|
|{"time":146950286...|
|{"time":146950286...|
|{"time":146950286...|
|{"time":146950286...|
+--------------------+
only showing top 5 rows

In [23]:
val vls = jsonDF.select("value").collect()

vls: Array[org.apache.spark.sql.Row] =
Array([{"time":1469502863,"action":"Close"}
], [{"time":1469502865,"action":"Open"}
], [{"time":1469502867,"action":"Open"}
], [{"time":1469502867,"action":"Open"}
], [{"time":1469502868,"action":"Open"}
], [{"time":1469502873,"action":"Open"}
], [{"time":1469502880,"action":"Close"}
], [{"time":1469502881,"action":"Close"}
], [{"time":1469502886,"action":"Open"}
], [{"time":1469502887,"action":"Open"}
], [{"time":1469502887,"action":"Open"}
], [{"time":1469502893,"action":"Close"}
], [{"time":1469502897,"action":"Open"}
], [{"time":1469502907,"action":"Open"}
], [{"time":1469502907,"action":"Open"}
], [{"time":1469502911,"action":"Close"}
], [{"time":1469502912,"action":"Open"}
], [{"time":1469502913,"action":"Open"}
], [{"time":1469502919,"action...

In [39]:
val s=vls(1).getString(0)

s: String =
"{"time":1469502865,"action":"Open"}
"

In [57]:
s(0)


res23: Char = {

In [85]:
import org.json4s.{DefaultFormats, MappingException}
import org.json4s.jackson.JsonMethods._
import org.apache.spark.sql.functions._

def getJsonKey(jsonstring: String): (String) = {
    implicit val formats = DefaultFormats
    val parsedJson = parse(jsonstring)  
    val key = (parsedJson \ "time").extract[String]
    key
}
val getJsonKeyUDF = udf((jsonstring: String) => getJsonKey(jsonstring))


val newDF = jsonDF.withColumn("key", getJsonKeyUDF(jsonDF("value"))).withColumn("json", jsonDF("value")).select("key", "json")
newDF.show

+----------+--------------------+
|       key|                json|
+----------+--------------------+
|1469502863|{"time":146950286...|
|1469502865|{"time":146950286...|
|1469502867|{"time":146950286...|
|1469502867|{"time":146950286...|
|1469502868|{"time":146950286...|
|1469502873|{"time":146950287...|
|1469502880|{"time":146950288...|
|1469502881|{"time":146950288...|
|1469502886|{"time":146950288...|
|1469502887|{"time":146950288...|
|1469502887|{"time":146950288...|
|1469502893|{"time":146950289...|
|1469502897|{"time":146950289...|
|1469502907|{"time":146950290...|
|1469502907|{"time":146950290...|
|1469502911|{"time":146950291...|
|1469502912|{"time":146950291...|
|1469502913|{"time":146950291...|
|1469502919|{"time":146950291...|
|1469502920|{"time":146950292...|
+----------+--------------------+
only showing top 20 rows

In [54]:
val array = new Array[String](3)
array(0)=vls(1).getString(0)
array(1)= vls(2).getString(0)
array(2)= vls(3).getString(0)
array.take(1)

res21: Array[String] =
Array("{"time":1469502865,"action":"Open"}
")

In [41]:
val events = sc.parallelize(
  """{"action":"create","timestamp":1452121277}""" ::
  """{"action":"create","timestamp":"1452121277"}""" ::
  """{"action":"create","timestamp":""}""" ::
  """{"action":"create","timestamp":null}""" ::
  """{"action":"create","timestamp":"null"}""" ::
  Nil
)


events: org.apache.spark.rdd.RDD[String] = ParallelCollectionRDD[6] at parallelize at <console>:25

In [49]:
events.take(1)

res11: Array[String] = Array({"action":"create","timestamp":1452121277})

In [48]:
import org.apache.spark.sql.types._

val schema = (new StructType).add("action", StringType).add("timestamp", LongType)

val test2= spark.read.schema(schema).json(events).show

+------+----------+
|action| timestamp|
+------+----------+
|create|1452121277|
|  null|      null|
|create|      null|
|create|      null|
|  null|      null|
+------+----------+

test2: Unit = ()

In [14]:
import org.apache.spark.sql.Row
import org.apache.spark.sql.types._

def convertRowToJson(row: Row): String = {

  val jsonSchema = new StructType().add("time",TimestampType).add("action", StringType)

      return spark.createDataFrame(row, jsonSchema).toJSON
}

<console>:44: error: overloaded method value createDataFrame with alternatives:
  (data: java.util.List[_],beanClass: Class[_])org.apache.spark.sql.DataFrame <and>
  (rdd: org.apache.spark.api.java.JavaRDD[_],beanClass: Class[_])org.apache.spark.sql.DataFrame <and>
  (rdd: org.apache.spark.rdd.RDD[_],beanClass: Class[_])org.apache.spark.sql.DataFrame <and>
  (rows: java.util.List[org.apache.spark.sql.Row],schema: org.apache.spark.sql.types.StructType)org.apache.spark.sql.DataFrame <and>
  (rowRDD: org.apache.spark.api.java.JavaRDD[org.apache.spark.sql.Row],schema: org.apache.spark.sql.types.StructType)org.apache.spark.sql.DataFrame <and>
  (rowRDD: org.apache.spark.rdd.RDD[org.apache.spark.sql.Row],schema: org.apache.spark.sql.types.StructType)org.apache.spark.sql.DataFrame
 cannot be applied to (org.apache.spark.sql.Row, org.apache.spark.sql.types.StructType)
             return spark.createDataFrame(row, jsonSchema).toJSON
                          ^


In [16]:
val test = spark.read.json(vls(1))

<console>:43: error: overloaded method value json with alternatives:
  (jsonRDD: org.apache.spark.rdd.RDD[String])org.apache.spark.sql.DataFrame <and>
  (jsonRDD: org.apache.spark.api.java.JavaRDD[String])org.apache.spark.sql.DataFrame <and>
  (paths: String*)org.apache.spark.sql.DataFrame <and>
  (path: String)org.apache.spark.sql.DataFrame
 cannot be applied to (org.apache.spark.sql.Row)
       val test = spark.read.json(vls(1))
                             ^


In [27]:

val rowRDD: RDD[Row] = spark.makeRDD(vls(1))

<console>:27: error: not found: type RDD
       val rowRDD: RDD[Row] = spark.makeRDD(vls(1))
                   ^
<console>:27: error: value makeRDD is not a member of org.apache.spark.sql.SparkSession
       val rowRDD: RDD[Row] = spark.makeRDD(vls(1))
                                    ^


In [18]:
def row2Json(row: Row, sqlContext: spark): String = {
  import sqlContext.implicits._
  val rowRDD: RDD[Row] = sqlContext.sparkContext.makeRDD(row :: Nil)
  val dataframe = sqlContext.createDataFrame(rowRDD, row.schema)
  dataframe.toJSON.first
}

<console>:39: error: not found: type spark
       def row2Json(row: Row, sqlContext: spark): String = {
                                          ^
<console>:41: error: not found: type RDD
         val rowRDD: RDD[Row] = sqlContext.sparkContext.makeRDD(row :: Nil)
                     ^


In [20]:
val sc: spark // An existing SparkContext.
val sqlContext = new org.apache.spark.sql.SQLContext(sc)

// this is used to implicitly convert an RDD to a DataFrame.
import sqlContext.implicits._

<console>:39: error: not found: type spark
       val sc: spark // An existing SparkContext.
               ^


###### loading json in spark sql databricks blog.


In [51]:
import org.apache.spark.sql.types._
val jsonSchema = new StructType().add("time",TimestampType).add("action", StringType)

val inputPath2 = "wasbs:///HdiSamples/databrick/*.json"

val staticInputDF2 = spark.read.schema(jsonSchema).json(inputPath2)

staticInputDF2: org.apache.spark.sql.DataFrame = [time: timestamp, action: string]

In [52]:
staticInputDF2.show(5)

+----+------+
|time|action|
+----+------+
|null|  null|
|null|  null|
|null|  null|
|null|  null|
|null|  null|
+----+------+
only showing top 5 rows

In [22]:
%%sql 
select value from counts5

###### This the end of simple word count example. 

In [74]:
val q = streammingInputDF2.writeStream.format("console").queryName("counts").outputMode("append").start()

q: org.apache.spark.sql.streaming.StreamingQuery = Streaming Query - counts [state = ACTIVE]

In [61]:
streammingInputDF2.isStreaming
streammingInputDF2.printSchema

root
 |-- key: binary (nullable = true)
 |-- value: binary (nullable = true)
 |-- topic: string (nullable = true)
 |-- partition: integer (nullable = true)
 |-- offset: long (nullable = true)
 |-- timestamp: timestamp (nullable = true)
 |-- timestampType: integer (nullable = true)

In [70]:
val df =streammingInputDF2.selectExpr("CAST(key AS STRING)","CAST (value as STRING)").as[(String,String)]

df: org.apache.spark.sql.Dataset[(String, String)] = [key: string, value: string]

In [50]:
streammingInputDF

<console>:48: error: value show is not a member of org.apache.spark.sql.streaming.StreamingQuery
       streammingInputDF.writeStream.start().show(5)
                                             ^


In [45]:
streammingInputDF.select("timestamp")

res59: org.apache.spark.sql.DataFrame = [timestamp: timestamp]

In [21]:
val streamingCountsDF = streammingInputDF.groupBy($"action",window($"time","1 hour")).count()
streamingCountsDF.isStreaming

<console>:37: error: not found: value streamingCountsDF
       streamingCountsDF.isStreaming
       ^


In [36]:
%%sql 
select action, date_format(window.end, "MMM-dd HH:mm") as time, count from counts order by time, action

An error was encountered:
org.apache.spark.sql.AnalysisException: cannot resolve '`action`' given input columns: [timestamp, value, key, timestampType, partition, offset, topic]; line 1 pos 7;
'Sort ['time ASC, 'action ASC], true
+- 'Project ['action, 'date_format('window.end, MMM-dd HH:mm) AS time#254, 'count]
   +- SubqueryAlias counts
      +- MemoryPlan MemorySink, [key#238, value#239, topic#240, partition#241, offset#242L, timestamp#243, timestampType#244]

  at org.apache.spark.sql.catalyst.analysis.package$AnalysisErrorAt.failAnalysis(package.scala:42)
  at org.apache.spark.sql.catalyst.analysis.CheckAnalysis$$anonfun$checkAnalysis$1$$anonfun$apply$2.applyOrElse(CheckAnalysis.scala:77)
  at org.apache.spark.sql.catalyst.analysis.CheckAnalysis$$anonfun$checkAnalysis$1$$anonfun$apply$2.applyOrElse(CheckAnalysis.scala:74)
  at org.apache.spark.sql.catalyst.trees.TreeNode$$anonfun$transformUp$1.apply(TreeNode.scala:308)
  at org.apache.spark.sql.catalyst.trees.TreeNode$$anonfun$tran

In [19]:
import org.apache.spark.sql.functions.{explode, split}
val events = spark.readStream.format("kafka").option("kafka.bootstrap.servers",kafkaBrokers).option("subscribe",topic).option("startingOffsets","earliest").load()

events: org.apache.spark.sql.DataFrame = [key: binary, value: binary ... 5 more fields]

In [29]:
val qevents = events.writeStream.format("memory").queryName("counts").outputMode("append").start()

qevents: org.apache.spark.sql.streaming.StreamingQuery = Streaming Query - counts [state = ACTIVE]

In [99]:
%%sql 
select * from counts2

An error was encountered:
org.apache.spark.sql.AnalysisException: Table or view not found: counts2; line 1 pos 14
  at org.apache.spark.sql.catalyst.analysis.package$AnalysisErrorAt.failAnalysis(package.scala:42)
  at org.apache.spark.sql.catalyst.analysis.Analyzer$ResolveRelations$.org$apache$spark$sql$catalyst$analysis$Analyzer$ResolveRelations$$lookupTableFromCatalog(Analyzer.scala:456)
  at org.apache.spark.sql.catalyst.analysis.Analyzer$ResolveRelations$$anonfun$apply$8.applyOrElse(Analyzer.scala:475)
  at org.apache.spark.sql.catalyst.analysis.Analyzer$ResolveRelations$$anonfun$apply$8.applyOrElse(Analyzer.scala:460)
  at org.apache.spark.sql.catalyst.plans.logical.LogicalPlan$$anonfun$resolveOperators$1.apply(LogicalPlan.scala:61)
  at org.apache.spark.sql.catalyst.plans.logical.LogicalPlan$$anonfun$resolveOperators$1.apply(LogicalPlan.scala:61)
  at org.apache.spark.sql.catalyst.trees.CurrentOrigin$.withOrigin(TreeNode.scala:69)
  at org.apache.spark.sql.catalyst.plans.logical.

In [30]:
qevents

res16: org.apache.spark.sql.streaming.StreamingQuery = Streaming Query - counts [state = TERMINATED]